# Apm data in Jupyter Notebook

This notebook describes integration of apm data. The goal is to show some basic reporting options that are possible with Oracle APM solution. The integration is based on provided OCI service endpoint. 


## Configuration and initialization

### The imports
This code contains the modules used in the notebook. Make sure to have these modules installed This can be done e.g. with pip:
```
pip install oci
pip install pandas
pip install logging
pip install plotly
```

In [1]:
import oci
from datetime import datetime
from datetime import timedelta
from IPython.display import display, JSON
import pandas as pd
import logging
import plotly.express as px


### The defaults
This piece of code needs to be updated to match your environment.

In [ ]:
# The Apm Domain ID ocid
APM_DOMAIN_ID = "ocid1.apmdomain.oc1.phx.amaaaaaagpihjxqaw3vdq3ekbdwl3rhpircgr6bisevciixdprto6eeettyq"

# the name of the profile to use (DEFAULT) 
OCI_PROFILE="DEFAULT"

# queries timeframe 'end' now 
# when notebook is intended to report 
# a specific period this should be set here.
QRY_BASE_TIME = datetime.utcnow()

# query data from 'now' going back 48 hours
TIME_BLOCK=timedelta(days=7)

# location of config file (~/.oci/config on linux)
OCI_LOC=oci.config.DEFAULT_LOCATION

# The number of rows returned in rest response
MAX_NUMBER_OF_ROWS=100


### Initializing code
Some code to initialize the client with relevant credentials and the logic to map apm response into pandas format.

In [ ]:
# create logger
logger = logging.getLogger(__name__)

# initialize configuration
oci_config = oci.config.from_file(OCI_LOC,OCI_PROFILE)
oci_signer = oci.signer.Signer(
            oci_config["tenancy"],
            oci_config["user"],
            oci_config["fingerprint"],
            oci_config["key_file"],
            oci_config.get("pass_phrase"),
        )
# initialize the query client
apmQC = oci.apm_traces.QueryClient(oci_config, signer=oci_signer)

# function mapping restApi response to pandas structure
def data2pandas(resp):
    fieldNames=[]
    resultData={}
    if (resp and resp.data and resp.data.query_result_metadata_summary):
        if (resp.data.query_result_metadata_summary.source_name == "TRACES" or resp.data.query_result_metadata_summary.source_name == "SPANS"):
            # preserve data
            for h in resp.data.query_result_metadata_summary.query_result_row_type_summaries:
                if (h.data_type=="STRING" or h.data_type=="NUMERIC"):
                    fieldNames.append(h.display_name)
                    resultData[h.display_name]=[]
                else:
                    logger.info(f"Ignoring response column {h.display_name} since {h.data_type} is not supported yet.")
                    
            # now enumerate the resulting rows
            for r in resp.data.query_result_rows:
                for col in fieldNames:
                    resultData[col].append(r.query_result_row_data[col])
                    logger.debug(f"Stored row data for {col}")                       
        else:
            logger.error("Unexpected source, requires special parsing")
    else:
        logger.error("Unexpected response, no result metadata")
    return pd.DataFrame(resultData, columns=fieldNames)


# Sample query

Below some sample query that uses the functions to get desired data and visualize the result in a table
This table shows some performance and load metrics grouped by web-application

In [ ]:

QRY_TEXT= """
   show (traces) WebApplicationName as WebApp, avg(ApdexScore) as Apdex, 
            count_distinct(userName) as users,
            sum(Pageviews)/count_distinct(sessionId) as avgPvsPerSes,
            sum(PageViews) as PageViews,
            count(*) as Traces, unique_values(ApmrumType) as ApmrumType,
            unique_values(ApmrumPageUpdateType) as PageUpdateType,
            count_distinct(sessionId) as sessions,
            avg(PageResponseTime) as AvgPageResponseTime,
            max(PageResponseTime) as maxPageResponseTime, avg(ConnectTime) as AvgConnectTime,
            sum(ErrorCount) as Errors 
        where component='BROWSER' and (ApmrumContextType<>'Background' or 
            ApmrumContextType is omitted)
        group by WebApplicationName
        order by WebApplicationName asc, max(PageResponseTime)
   """

data = apmQC.query(apm_domain_id=APM_DOMAIN_ID,
        time_span_started_greater_than_or_equal_to=QRY_BASE_TIME - TIME_BLOCK,
        time_span_started_less_than=QRY_BASE_TIME,
        query_details=oci.apm_traces.models.QueryDetails(query_text=QRY_TEXT),
        limit=MAX_NUMBER_OF_ROWS,
        page="1")

data2pandas(data)

# Alternative sample query
Query that shows data from a set of sessions. The data contains the top (most) active sessions. 

In [ ]:
QRY_TEXT= """
      show traces SessionId, WebApplicationName, sum(PageViews) as TotalPageviews,
            sum(ErrorCount) as TotalErrors,
            max(TraceLatestSpanEndTime)-min(TraceFirstSpanStartTime) as SessionDuration
        group by sessionId, webApplicationName
        order by sum(PageViews) desc
   """

data = apmQC.query(apm_domain_id=APM_DOMAIN_ID,
        time_span_started_greater_than_or_equal_to=QRY_BASE_TIME - TIME_BLOCK,
        time_span_started_less_than=QRY_BASE_TIME,
        query_details=oci.apm_traces.models.QueryDetails(query_text=QRY_TEXT),
        limit=MAX_NUMBER_OF_ROWS,
        page="1")

sespanda=data2pandas(data)


sespanda["SessionDurationTD"]=sespanda["SessionDuration"].apply(lambda ms: 
                                    timedelta(milliseconds=ms))
sespanda["SessionDurationTS"]=sespanda["SessionDuration"].apply(lambda ms: 
                                    datetime(1970,1,1,0,0,0) + timedelta(milliseconds=ms))

sespanda.loc[:, sespanda.columns.difference(["SessionDurationTS", "SessionDuration"])]

In [ ]:

fig = px.scatter(sespanda, x="TotalPageviews", y="SessionDurationTS", 
                 color="WebApplicationName", size="TotalErrors", 
                 hover_data=["SessionId","TotalPageviews","SessionDurationTD"],
                 labels=dict(TotalPageviews="Total Pageviews", SessionDuration="Session Duration")
                )

fig.update_yaxes( type="date",tickformat="%-j days %Hh %Mm %S sec" )

fig.show()